## Code for preparing the South Korean COVID-19 patient location data for the privacy attack.

In [1]:
import pandas as pd
import numpy as np
import csv
import os
import sys
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
%matplotlib inline

# import privacy attack
# !pip install git+https://github.com/GilianPonte/likelihood_based_privacy_attack.git
from likelihood_based_privacy_attack import attacks

# Add the parent directory to path
sys.path.append('../..')

# Then import
from helper_functions import *

Import the cleaned SK data.

In [2]:
sk_data = pd.read_csv("../../../Data/SK/cleaned_sk_data.csv")

In [3]:
sk_data

latitude  longitude  sex  age  state
0     0.944157  -1.010655    1    5      0
1     0.889746  -0.694899    1    5      0
2     0.917482  -0.682299    1    3      0
3     0.916660  -0.682551    1    3      0
4     0.886074  -0.668883    1    3      0
...        ...        ...  ...  ...    ...
6707  0.881500  -0.925307    1    4      0
6708 -1.728784   1.470871    1    4      0
6709 -1.548071   1.557316    1    4      0
6710 -1.549392   1.555785    1    4      0
6711 -1.548071   1.557316    1    4      0

[6712 rows x 5 columns]

Drop duplicates.

In [4]:
sk_data = pd.DataFrame.drop_duplicates(sk_data)

In [5]:
# reset dataframe index
sk_data.reset_index(drop=True, inplace=True)
print(sk_data)

      latitude  longitude  sex  age  state
0     0.944157  -1.010655    1    5      0
1     0.889746  -0.694899    1    5      0
2     0.917482  -0.682299    1    3      0
3     0.916660  -0.682551    1    3      0
4     0.886074  -0.668883    1    3      0
...        ...        ...  ...  ...    ...
3802 -1.662973   1.164819    1    2      0
3803 -1.558049   0.964307    1    6      0
3804 -1.622048   0.866628    1    6      0
3805 -1.548071   1.557316    1    4      0
3806 -1.549392   1.555785    1    4      0

[3807 rows x 5 columns]


### Perform the privacy attack simulation

The steps are as follows:

- Split the data three ways:
    - Marketer training data
    - Adversary training data
    - Outside data
- Train Marketer and Adversary synthesis models
- Compute predictions for distribution membership for outside data and compute empirical epsilon
- Repeat the above steps many times (100 iterations in Ponte et al. 2024)

#### Step 1: Split the data three ways

In [6]:
def train_test_split_even(X, train_size, random_state=None):
    # Split the data normally
    X_train, X_test = train_test_split(
        X, train_size=train_size, random_state=random_state
    )
    
    # If train set has odd number of rows
    if len(X_train) % 2 != 0:
        # Move the last row from train to test
        X_test = np.vstack([X_test, X_train[-1:]])
        X_train = X_train[:-1]
    
    return X_train, X_test

In [7]:
internal_data, external_data = train_test_split_even(sk_data, train_size=0.67)
marketer_train, adversary_train = train_test_split(internal_data, train_size=0.5)
print("Train data shape: ", marketer_train.shape)
print("Adversary data shape: ", adversary_train.shape)
print("External data shape: ", external_data.shape)

Train data shape:  (1275, 5)
Adversary data shape:  (1275, 5)
External data shape:  (1257, 5)


#### Train Marketer Synthesis Model

In [7]:
# synthesis steps
# written as a list of tuples (features, model)
synthesis_steps = [
    (['latitude', 'longitude'], 'gmm'),
    ('sex', 'multinomial'),
    ('age', 'multinomial'),
    ('state', 'multinomial')
]

In [8]:
# parameter bounds
param_bounds = {
    'gmm': {
        'num_components': (10, 200.99),
    },
    'multinomial': {
        'sex': {'C': (0.001, 3)},
        'age': {'C': (0.001, 3)},
        'state': {'C': (0.001, 3)}
    }
}

In [9]:
number_synthetic_datasets=3
num_iter_optimization=5
num_init_optimization=2
poly_degree_mnl=2
poly_degree_pmse=2
random_states = [1006, 428]

In [11]:
marketer_optimization_results = [optimize_models(train_data=marketer_train, 
                                                 number_synthetic_datasets=number_synthetic_datasets,
                                                 synthesis_steps=synthesis_steps,
                                                 param_bounds=param_bounds,
                                                 random_state=r,
                                                 poly_degree_mnl=poly_degree_mnl,
                                                 poly_degree_pmse=poly_degree_pmse,
                                                 num_iter_optimization=num_iter_optimization,
                                                 num_init_optimization=num_init_optimization) for r in random_states]

|   iter    |  target   |    x0     |    x1     |    x2     |    x3     |
-------------------------------------------------------------------------


c:\Users\camer\anaconda3\Lib\site-packages\joblib\externals\loky\backend\context.py:136: UserWarning: Could not find the number of physical cores for the following reason:
[WinError 2] The system cannot find the file specified
Returning the number of logical cores instead. You can silence this warning by setting LOKY_MAX_CPU_COUNT to the number of cores you want to use.
  warnings.warn(
  File "c:\Users\camer\anaconda3\Lib\site-packages\joblib\externals\loky\backend\context.py", line 257, in _count_physical_cores
    cpu_info = subprocess.run(
        "wmic CPU Get NumberOfCores /Format:csv".split(),
        capture_output=True,
        text=True,
    )
  File "c:\Users\camer\anaconda3\Lib\subprocess.py", line 554, in run
    with Popen(*popenargs, **kwargs) as process:
         ~~~~~^^^^^^^^^^^^^^^^^^^^^^
  File "c:\Users\camer\anaconda3\Lib\subprocess.py", line 1039, in __init__
    self._execute_child(args, executable, preexec_fn, close_fds,
    ~~~~~~~~~~~~~~~~~~~^^^^^^^^^^^^^^^^^^

| 2         | -0.155460 | 151.92989 | 0.6800465 | 1.9279589 | 2.6471840 |


c:\Users\camer\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1419: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(
c:\Users\camer\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1419: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(
c:\Users\camer\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1419: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(
c:\Users\camer\anaconda3\Lib\site-packages\sklearn\linear_model\_sag.py:348: ConvergenceWarning: The max_iter was reached which means th

| 3         | -0.196032 | 151.46605 | 2.1640693 | 0.8867481 | 1.5770236 |


...

| 29        | -0.133000 | 37.275902 | 0.3875378 | 0.5932353 | 0.4464087 |


c:\Users\camer\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1419: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(
c:\Users\camer\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1419: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(
c:\Users\camer\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1419: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(
c:\Users\camer\anaconda3\Lib\site-packages\sklearn\linear_model\_sag.py:348: ConvergenceWarning: The max_iter was reached which means th

| 30        | -0.206394 | 156.17046 | 1.5205118 | 2.4556686 | 1.1596393 |


c:\Users\camer\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1419: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(
c:\Users\camer\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1419: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(
c:\Users\camer\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1419: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(
c:\Users\camer\anaconda3\Lib\site-packages\sklearn\linear_model\_sag.py:348: ConvergenceWarning: The max_iter was reached which means th

| 31        | -0.001862 | 68.717735 | 2.9008397 | 0.0327364 | 0.5656713 |


In [12]:
adversary_optimization_results = [optimize_models(train_data=adversary_train, 
                                                  number_synthetic_datasets=number_synthetic_datasets,
                                                  synthesis_steps=synthesis_steps,
                                                  param_bounds=param_bounds,
                                                  random_state=r,
                                                  poly_degree_mnl=poly_degree_mnl,
                                                  poly_degree_pmse=poly_degree_pmse,
                                                  num_iter_optimization=num_iter_optimization,
                                                  num_init_optimization=num_init_optimization) for r in random_states]

|   iter    |  target   |    x0     |    x1     |    x2     |    x3     |
-------------------------------------------------------------------------


c:\Users\camer\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1419: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(
c:\Users\camer\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1419: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(
c:\Users\camer\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1419: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(
c:\Users\camer\anaconda3\Lib\site-packages\sklearn\linear_model\_sag.py:348: ConvergenceWarning: The max_iter was reached which means th

| 2         | -0.125849 | 151.92989 | 0.6800465 | 1.9279589 | 2.6471840 |


c:\Users\camer\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1419: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(
c:\Users\camer\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1419: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(
c:\Users\camer\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1419: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(
c:\Users\camer\anaconda3\Lib\site-packages\sklearn\linear_model\_sag.py:348: ConvergenceWarning: The max_iter was reached which means th

| 3         | -0.128898 | 151.46605 | 2.1640693 | 0.8867481 | 1.5770236 |


...

| 29        | -0.097069 | 37.275902 | 0.3875378 | 0.5932353 | 0.4464087 |


c:\Users\camer\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1419: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(
c:\Users\camer\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1419: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(
c:\Users\camer\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1419: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(
c:\Users\camer\anaconda3\Lib\site-packages\sklearn\linear_model\_sag.py:348: ConvergenceWarning: The max_iter was reached which means th

| 30        | -0.098003 | 10.265409 | 1.6255407 | 2.8937851 | 1.3503284 |


c:\Users\camer\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1419: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(
c:\Users\camer\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1419: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(
c:\Users\camer\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1419: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(
c:\Users\camer\anaconda3\Lib\site-packages\sklearn\linear_model\_sag.py:348: ConvergenceWarning: The max_iter was reached which means th

| 31        | -0.155909 | 106.88091 | 1.6834080 | 1.2290456 | 1.5035547 |


#### Generate one synthetic data set each from the Marketer and Adversary synthesis models

In [13]:
best_marketer_params = marketer_optimization_results[np.argmin([x['best_score'] for x in marketer_optimization_results])]['best_params']

best_marketer_params

{'gmm': {'num_components': 68},
 'multinomial': {'sex': {'C': np.float64(2.9008397335746405)},
  'age': {'C': np.float64(0.03273642505794086)},
  'state': {'C': np.float64(0.5656713706788853)}}}

In [14]:
marketer_ratios, marketer_sXs = perform_synthesis(
    train_data=marketer_train,
    number_synthetic_datasets=20,
    synthesis_steps=synthesis_steps,
    param_values=best_marketer_params
)

c:\Users\camer\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1419: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(
c:\Users\camer\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1419: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(
c:\Users\camer\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1419: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(
c:\Users\camer\anaconda3\Lib\site-packages\sklearn\linear_model\_sag.py:348: ConvergenceWarning: The max_iter was reached which means th

In [15]:
best_adversary_params = adversary_optimization_results[np.argmin([x['best_score'] for x in adversary_optimization_results])]['best_params']

best_adversary_params

{'gmm': {'num_components': 151},
 'multinomial': {'sex': {'C': np.float64(0.659123991978081)},
  'age': {'C': np.float64(0.04802110810890377)},
  'state': {'C': np.float64(1.2411189655984587)}}}

In [16]:
adversary_ratios, adversary_sXs = perform_synthesis(
    train_data=adversary_train,
    number_synthetic_datasets=20,
    synthesis_steps=synthesis_steps,
    param_values=best_adversary_params
)

c:\Users\camer\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1419: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(
c:\Users\camer\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1419: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(
c:\Users\camer\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1419: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(
c:\Users\camer\anaconda3\Lib\site-packages\sklearn\linear_model\_sag.py:348: ConvergenceWarning: The max_iter was reached which means th

In [17]:
print(np.mean(marketer_ratios))
print(np.mean(adversary_ratios))

0.926743120879532
0.7462709517791926


In [18]:
marketer_synthetic = marketer_sXs[0]
adversary_synthetic = adversary_sXs[0]

#### Apply Privacy Attack

In [19]:
# apply privacy attack
attack_results = attacks.privacy_attack(seed = 1, 
                       simulations = 1, 
                       train = marketer_train, 
                       adversary = adversary_train, 
                       outside_training = external_data,
                       protected_training = marketer_synthetic, 
                       protected_adversary = adversary_synthetic)

iteration is 0
FPR is 0.12649164677804295
FNR is 0.855686274509804
TPR is 0.14431372549019608
TNR is 0.8735083532219571
empirical epsilon = 0.07593284799201845


In [20]:
attack_results[0][0]

np.float64(0.07593284799201845)

## Set Everything Up in a Loop

In [10]:
num_simulations = 100
epsilons = list()
seed = 42

In [11]:
for i in range(num_simulations):

    # split data
    internal_data, external_data = train_test_split_even(sk_data, train_size=0.67, random_state=seed+i)
    marketer_train, adversary_train = train_test_split(internal_data, train_size=0.5)

    # marketer synthesis
    marketer_optimization_results = [optimize_models(train_data=marketer_train, 
                                                     number_synthetic_datasets=number_synthetic_datasets,
                                                     synthesis_steps=synthesis_steps,
                                                     param_bounds=param_bounds,
                                                     random_state=r,
                                                     poly_degree_mnl=poly_degree_mnl,
                                                     poly_degree_pmse=poly_degree_pmse,
                                                     num_iter_optimization=num_iter_optimization,
                                                     num_init_optimization=num_init_optimization) for r in random_states]

    # adversary synthesis
    adversary_optimization_results = [optimize_models(train_data=adversary_train, 
                                                      number_synthetic_datasets=number_synthetic_datasets,
                                                      synthesis_steps=synthesis_steps,
                                                      param_bounds=param_bounds,
                                                      random_state=r,
                                                      poly_degree_mnl=poly_degree_mnl,
                                                      poly_degree_pmse=poly_degree_pmse,
                                                      num_iter_optimization=num_iter_optimization,
                                                      num_init_optimization=num_init_optimization) for r in random_states]

    # store best params
    best_marketer_params = marketer_optimization_results[np.argmin([x['best_score'] for x in marketer_optimization_results])]['best_params']
    best_adversary_params = adversary_optimization_results[np.argmin([x['best_score'] for x in adversary_optimization_results])]['best_params']

    # train and generate with best params
    marketer_ratios, marketer_sXs = perform_synthesis(
        train_data=marketer_train,
        number_synthetic_datasets=20,
        synthesis_steps=synthesis_steps,
        param_values=best_marketer_params
    )

    adversary_ratios, adversary_sXs = perform_synthesis(
        train_data=adversary_train,
        number_synthetic_datasets=20,
        synthesis_steps=synthesis_steps,
        param_values=best_adversary_params
    )

    marketer_synthetic = marketer_sXs[0]
    adversary_synthetic = adversary_sXs[0]

    # apply privacy attack
    attack_results = attacks.privacy_attack(seed = 1, 
                                            simulations = 1, 
                                            train = marketer_train, 
                                            adversary = adversary_train, 
                                            outside_training = external_data,
                                            protected_training = marketer_synthetic, 
                                            protected_adversary = adversary_synthetic)

    epsilons.append(attack_results[0][0])

    
    

|   iter    |  target   |    x0     |    x1     |    x2     |    x3     |
-------------------------------------------------------------------------


c:\Users\camer\anaconda3\Lib\site-packages\joblib\externals\loky\backend\context.py:136: UserWarning: Could not find the number of physical cores for the following reason:
[WinError 2] The system cannot find the file specified
Returning the number of logical cores instead. You can silence this warning by setting LOKY_MAX_CPU_COUNT to the number of cores you want to use.
  warnings.warn(
  File "c:\Users\camer\anaconda3\Lib\site-packages\joblib\externals\loky\backend\context.py", line 257, in _count_physical_cores
    cpu_info = subprocess.run(
        "wmic CPU Get NumberOfCores /Format:csv".split(),
        capture_output=True,
        text=True,
    )
  File "c:\Users\camer\anaconda3\Lib\subprocess.py", line 554, in run
    with Popen(*popenargs, **kwargs) as process:
         ~~~~~^^^^^^^^^^^^^^^^^^^^^^
  File "c:\Users\camer\anaconda3\Lib\subprocess.py", line 1039, in __init__
    self._execute_child(args, executable, preexec_fn, close_fds,
    ~~~~~~~~~~~~~~~~~~~^^^^^^^^^^^^^^^^^^

| 2         | -0.079248 | 151.92989 | 0.6800465 | 1.9279589 | 2.6471840 |


c:\Users\camer\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1419: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(
c:\Users\camer\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1419: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(


| 3         | -0.099279 | 151.46605 | 2.1640693 | 0.8867481 | 1.5770236 |


...

| 7         | -0.267541 | 19.711711 | 1.6883680 | 0.2214611 | 2.5391899 |


c:\Users\camer\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1419: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(
c:\Users\camer\anaconda3\Lib\site-packages\sklearn\linear_model\_sag.py:348: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(
c:\Users\camer\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1419: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(
c:\Users\camer\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1419: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment var

| 8         | -0.291050 | 101.47982 | 2.0738882 | 0.9739028 | 2.4791084 |


c:\Users\camer\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1419: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(
c:\Users\camer\anaconda3\Lib\site-packages\sklearn\linear_model\_sag.py:348: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(
c:\Users\camer\anaconda3\Lib\site-packages\sklearn\linear_model\_sag.py:348: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(
c:\Users\camer\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1419: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(
c:\Users\camer\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.p

iteration is 0
FPR is 0.13126491646778043
FNR is 0.8533333333333333
TPR is 0.14666666666666667
TNR is 0.8687350835322196
empirical epsilon = 0.05598600967096996


In [13]:
np.max(epsilons)

np.float64(0.43389718003790645)